In [1]:
from google.transit import gtfs_realtime_pb2
import requests
from collections import defaultdict
import time
from datetime import datetime
import pandas as pd
from copy import deepcopy
import schedule
from ST_DBSCAN.stdbscan import STDBSCAN
import sys
from tqdm import tqdm
import folium
from folium.plugins import MarkerCluster
from folium.plugins import Search
from collections import Counter

# read entity data from protobuffer
def get_entity_data(entity):
    vehicle_id = entity.vehicle.vehicle.id
    vehicle_lat = entity.vehicle.position.latitude
    vehicle_lon = entity.vehicle.position.longitude
    vehicle_route_id = str(int(float(entity.vehicle.trip.route_id)))
    vehicle_timestamp = entity.vehicle.timestamp
    return vehicle_id, vehicle_lat, vehicle_lon, vehicle_route_id, vehicle_timestamp


def read_feed():
    # print(OTD_RT_URL)
    feed = gtfs_realtime_pb2.FeedMessage()
    try:
        response = requests.get(OTD_RT_URL)
        feed.ParseFromString(response.content)
        # print("Feed at " + str(datetime.datetime.now()))
    except TimeoutError:
        print("URL Timeout")
    except requests.exceptions.ConnectionError:
        print('Max retries exceeded')
    return feed


def run_db_scan(df, spatial_threshold=50, temporal_threshold=20, min_neighbors=12):
    if len(df) == 0:
        print(df)
    st_dbscan = STDBSCAN(col_lat='lat', col_lon='lng',
                         col_time='timestamp', spatial_threshold=spatial_threshold,
                         temporal_threshold=temporal_threshold, min_neighbors=min_neighbors)
    df = st_dbscan.projection(df, p1_str='epsg:4326', p2_str='epsg:32635')
    result_t600 = st_dbscan.run(df)
    return result_t600


def save_to_dict():
    global remove_element_flag
    feed = read_feed()
    # print(feed)
    if time.time() - process_start_timestamp >= 1200:
        remove_element_flag = True
    for entity in feed.entity:
        # print(entity)
        vehicle_id, vehicle_lat, vehicle_lon, vehicle_route_id, vehicle_timestamp = get_entity_data(entity)
        if pb_data_dict.get(vehicle_id):
            if not (datetime.fromtimestamp(int(vehicle_timestamp)) in pb_data_dict[vehicle_id]['timestamp'] and vehicle_lat in pb_data_dict[vehicle_id]['lat'] and vehicle_lon in pb_data_dict[vehicle_id]['lng'] and vehicle_route_id in pb_data_dict[vehicle_id]['route_id']):
                pb_data_dict[vehicle_id]['lat'].append(vehicle_lat)
                pb_data_dict[vehicle_id]['lng'].append(vehicle_lon)
                pb_data_dict[vehicle_id]['timestamp'].append(datetime.fromtimestamp(int(vehicle_timestamp)))
                pb_data_dict[vehicle_id]['route_id'].append(vehicle_route_id)
                if remove_element_flag:
                    print('deleted for ', vehicle_id)
                    if len(pb_data_dict[vehicle_id]['lat']) <= 1:
                        del pb_data_dict[vehicle_id]
                    else:
                        pb_data_dict[vehicle_id]['lat'].pop(0)
                        pb_data_dict[vehicle_id]['lng'].pop(0)
                        pb_data_dict[vehicle_id]['timestamp'].pop(0)
                        pb_data_dict[vehicle_id]['route_id'].pop(0)
        else:
            vehicle_data_dict = defaultdict(list)
            vehicle_data_dict['lat'].append(vehicle_lat)
            vehicle_data_dict['lng'].append(vehicle_lon)
            vehicle_data_dict['timestamp'].append(datetime.fromtimestamp(int(vehicle_timestamp)))
            vehicle_data_dict['route_id'].append(vehicle_route_id)
            
            pb_data_dict[vehicle_id] = vehicle_data_dict
    # print(pb_data_dict)


def calculate_centroid(list_of_coordinates):
    return sum(list_of_coordinates)/len(list_of_coordinates)


def cluster_json_data(bus, pb_data_dict):
    lat_list = pb_data_dict[bus]['lat']
    lng_list = pb_data_dict[bus]['lng']

    lat_centroid = calculate_centroid(lat_list)
    lng_centroid = calculate_centroid(lng_list)

#     timestamp = int(time.time())
    timestamp = pb_data_dict[bus]['timestamp'][-1]
    route_id = pb_data_dict[bus]['route_id'][0]

    bus_data = {'vehicle_id': bus, 'lat': lat_centroid, 'lng': lng_centroid, 'timestamp': timestamp, 'route_id' : route_id}

    return bus_data


def chk_cluster():
    global clustered_buses_list
    # production
    # spatial_threshold = 10
    # temporal_threshold = 900
    # min_neighbors = 90

    # testing (less time gap)
    spatial_threshold = 10
    temporal_threshold = 300
    min_neighbors = 30
    clustered_buses_data = []
    start = time.time()
    temp_list = list()
    print(len(pb_data_dict), "dict")
    for bus in tqdm(pb_data_dict.keys()):
        bus_data_df = pd.DataFrame.from_dict(pb_data_dict[bus])
#         return bus_data_df
        if len(bus_data_df) != 0:
            clustered_df = run_db_scan(deepcopy(bus_data_df), spatial_threshold=spatial_threshold,
                                       temporal_threshold=temporal_threshold, min_neighbors=min_neighbors)
#             return clustered_df
            bus_data_df['cluster'] = clustered_df['cluster']
            # unique_clusters = chk_if_cluster_close_to_depot(bus_data_df)
            unique_clusters = pd.unique(bus_data_df.cluster)
#             return bus_data_df
            if len(unique_clusters) > 1:
                bus_data = cluster_json_data(bus,pb_data_dict)
#                 print('cluster detected for ',bus,bus_data)
#                 print(pb_data_dict[bus])
                clustered_buses_data.append(bus_data)
                temp_list.append(bus)
            else:
#                 print('no cluster detected for ', bus)
                pass
    clustered_buses_list = temp_list
#     print(clustered_buses_list)
#     print(time.time() - start)
    return clustered_buses_data

def plot_map():
    prob_buses = chk_cluster()
    start_lat = 28.617453756786528
    start_lon = 77.20423389616467

    m=folium.Map(location=[start_lat,start_lon],tiles='Open Street Map', zoom_start=10)
    for i in prob_buses:
    #     print(i)
        lat = i['lat']
        lng = i['lng']
        folium.Circle(
          location=[lat, lng],
          popup=i['vehicle_id'],
          color='crimson',
          fill=True,
          fill_color='crimson'
       ).add_to(m)
    m.save('map1.html')
    

if __name__ == '__main__':
    OTD_API_KEY = 'X5xn9r7RQ8j2xAQgIMWA9p3BlJMMy28u'
    OTD_RT_URL = f'https://otd.delhi.gov.in/api/realtime/VehiclePositions.pb?key={OTD_API_KEY}'
    print('OTD API URL', OTD_RT_URL)

    pb_data_dict = {}
    clustered_buses_list = list()
    remove_element_flag = False
    process_start_timestamp = time.time()
    schedule.every(10).seconds.do(save_to_dict)
#     schedule.every(180).seconds.do(chk_cluster)
#     schedule.every(600).seconds.do(plot_map)
    counter = 0
    while counter < 600:
        schedule.run_pending()
        time.sleep(1)
        counter += 1
        print(counter)




OTD API URL https://otd.delhi.gov.in/api/realtime/VehiclePositions.pb?key=X5xn9r7RQ8j2xAQgIMWA9p3BlJMMy28u
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
2

KeyboardInterrupt: 

In [ ]:
# OTD_API_KEY = 'X5xn9r7RQ8j2xAQgIMWA9p3BlJMMy28u'
# OTD_RT_URL = f'https://otd.delhi.gov.in/api/realtime/VehiclePositions.pb?key={OTD_API_KEY}'
# print('OTD API URL', OTD_RT_URL)

# pb_data_dict = {}
# clustered_buses_list = list()
# remove_element_flag = False
# process_start_timestamp = time.time()

In [ ]:
# save_to_dict()

In [2]:
pb_data_dict

{'DL1PD1678': defaultdict(list,
             {'lat': [28.598974227905273,
               28.598634719848633,
               28.59564971923828,
               28.595739364624023,
               28.59575843811035,
               28.59577751159668,
               28.595823287963867,
               28.595834732055664,
               28.59583282470703,
               28.595821380615234,
               28.595809936523438,
               28.595809936523438,
               28.595813751220703,
               28.595827102661133,
               28.595834732055664,
               28.595834732055664,
               28.595823287963867,
               28.5958309173584,
               28.595840454101562,
               28.595848083496094,
               28.59585189819336,
               28.595867156982422,
               28.595857620239258,
               28.59588623046875,
               28.595882415771484,
               28.595863342285156,
               28.59585952758789,
               28.5958538

In [3]:
prob_buses = chk_cluster()

1878 dict


100%|██████████████████████████████████████████████████████████████████████████████| 1878/1878 [00:20<00:00, 91.04it/s]


In [4]:
len(prob_buses)

30

In [5]:
prob_buses


[{'vehicle_id': 'DL1PD5164',
  'lat': 28.635122033052667,
  'lng': 77.0617737880973,
  'timestamp': datetime.datetime(2022, 4, 15, 16, 22, 13),
  'route_id': '787'},
 {'vehicle_id': 'DL1PC5608',
  'lat': 28.492675185203552,
  'lng': 77.30356025695801,
  'timestamp': datetime.datetime(2022, 4, 15, 16, 22, 4),
  'route_id': '839'},
 {'vehicle_id': 'DL1PD4344',
  'lat': 28.660129637945268,
  'lng': 77.22787402925037,
  'timestamp': datetime.datetime(2022, 4, 15, 16, 22, 3),
  'route_id': '825'},
 {'vehicle_id': 'DL1PC4799',
  'lat': 28.660415749800833,
  'lng': 77.22586862664474,
  'timestamp': datetime.datetime(2022, 4, 15, 16, 22, 11),
  'route_id': '841'},
 {'vehicle_id': 'DL1PC6325',
  'lat': 28.591047075059677,
  'lng': 77.23793898688422,
  'timestamp': datetime.datetime(2022, 4, 15, 16, 22, 17),
  'route_id': '1016'},
 {'vehicle_id': 'DL1PD5077',
  'lat': 28.635569456146985,
  'lng': 77.09280656023724,
  'timestamp': datetime.datetime(2022, 4, 15, 16, 22, 14),
  'route_id': '638'},


In [6]:
cl1_bus_df = pd.DataFrame.from_dict(prob_buses)

In [ ]:
cl1_bus_df['timestamp'] = pd.to_datetime(cl1_bus_df['timestamp'], unit = 's')

In [7]:
cl1_bus_df

vehicle_id        lat        lng           timestamp route_id
0   DL1PD5164  28.635122  77.061774 2022-04-15 16:22:13      787
1   DL1PC5608  28.492675  77.303560 2022-04-15 16:22:04      839
2   DL1PD4344  28.660130  77.227874 2022-04-15 16:22:03      825
3   DL1PC4799  28.660416  77.225869 2022-04-15 16:22:11      841
4   DL1PC6325  28.591047  77.237939 2022-04-15 16:22:17     1016
5   DL1PD5077  28.635569  77.092807 2022-04-15 16:22:14      638
6   DL1PD5076  28.585063  76.981312 2022-04-15 16:22:09      523
7   DL1PD4272  28.707503  77.177995 2022-04-15 16:22:10      977
8   DL1PD4718  28.652741  77.108373 2022-04-15 16:22:04      700
9   DL1PD5040  28.612684  77.307163 2022-04-15 16:21:56      127
10  DL1PD2324  28.690814  77.101217 2022-04-15 16:22:00      581
11  DL1PD4997  28.617548  77.204251 2022-04-15 16:22:01      692
12  DL1PD4299  28.645958  77.315288 2022-04-15 16:21:57      882
13  DL1PC4858  28.703575  77.213302 2022-04-15 16:22:23      217
14  DL1PD2658  28.631683  77.091116 2022-04-15 16:22:17      228
15  DL1PD2817  28.673989  77.168855 2022-04-15 16:22:15      797
16  DL1PC6959  28.646771  77.314650 2022-04-15 16:22:19      208
17  DL1PD3003  28.637137  77.252761 2022-04-15 16:22:15       72
18  DL1PC5986  28.733050  77.172566 2022-04-15 16:22:17     1094
19  DL1PD5074  28.617032  77.338567 2022-04-15 16:22:06      237
20  DL1PD5029  28.718240  77.158348 2022-04-15 16:22:00      759
21  DL1PD4514  28.635459  77.252855 2022-04-15 16:22:23      213
22  DL1PD0547  28.646184  77.314666 2022-04-15 16:22:06      343
23  DL1PC5284  28.493356  77.303376 2022-04-15 16:22:16      839
24  DL1PD3534  28.586399  77.253150 2022-04-15 16:22:15     1186
25  DL1PD3315  28.646382  77.315011 2022-04-15 16:22:07      412
26  DL1PD4622  28.567107  77.065884 2022-04-15 16:22:13     1106
27  DL1PC5279  28.665726  77.230088 2022-04-15 16:22:19      339
28  DL1PD3692  28.646176  77.314627 2022-04-15 16:22:04      609
29  DL1PD5201  28.660225  77.226327 2022-04-15 16:22:08      507

In [ ]:
spatial_threshold = 300
temporal_threshold = 600
min_neighbors = 3
clustered_df2 = run_db_scan(deepcopy(cl1_bus_df), spatial_threshold=spatial_threshold,
                                       temporal_threshold=temporal_threshold, min_neighbors=min_neighbors)

In [ ]:
Counter(clustered_df2.cluster)

In [ ]:
clustered_df2